In [1]:
import yfinance as yf
import numpy as np
import pandas as pd

In [2]:
df_risk_off = yf.download(['XLU','XLV','XLP'],start = '1999-01-01',end = '2020-07-30')['Close']
df_risk_on = yf.download(['XLB','XLK','XLI','XLY'], start = '1999-01-01', end = '2020-07-30')['Close']
df_risk_off.tail()

[*********************100%***********************]  3 of 3 completed
[*********************100%***********************]  4 of 4 completed


XLP        XLU         XLV
Date                                        
2020-07-23  62.209999  60.680000  106.269997
2020-07-24  62.130001  60.279999  105.099998
2020-07-27  62.439999  59.549999  105.889999
2020-07-28  62.669998  60.450001  105.769997
2020-07-29  62.759998  60.730000  106.879997

In [3]:
df_risk_on.tail()

XLB        XLI         XLK         XLY
Date                                                    
2020-07-23  61.680000  72.419998  106.489998  135.300003
2020-07-24  61.470001  71.839996  105.199997  135.539993
2020-07-27  62.360001  72.139999  106.860001  136.380005
2020-07-28  60.990002  71.639999  105.610001  135.029999
2020-07-29  61.490002  72.730003  107.139999  136.399994

In [4]:
Portfolio_Risk_Off = np.array([1/3,1/3,1-2/3])
Portfolio_Risk_On = np.array([1/4,1/4,1/4,1/4])
df_risk_off= df_risk_off.pct_change()
df_risk_on=df_risk_on.pct_change()
df_risk_off

XLP       XLU       XLV
Date                                    
1999-01-04       NaN       NaN       NaN
1999-01-05  0.007541  0.012080  0.015663
1999-01-06  0.012090  0.010379  0.016607
1999-01-07 -0.011377 -0.003595 -0.004667
1999-01-08 -0.004028  0.005670  0.012309
...              ...       ...       ...
2020-07-23  0.003549  0.001155 -0.004497
2020-07-24 -0.001286 -0.006592 -0.011010
2020-07-27  0.004989 -0.012110  0.007517
2020-07-28  0.003684  0.015113 -0.001133
2020-07-29  0.001436  0.004632  0.010494

[5428 rows x 3 columns]

In [5]:
portfolio_rets_off= Portfolio_Risk_Off * df_risk_off
portfolio_rets_on= Portfolio_Risk_On * df_risk_on

In [6]:
df_risk_off['portfolio_rets_off'] = portfolio_rets_off.sum(axis=1)
df_risk_on['portfolio_rets_on']=portfolio_rets_on.sum(axis=1)

In [86]:
df_risk_off['portfolio_cum_rets_off'] = (1+df_risk_off['portfolio_rets_off']).cumprod()-1
df_risk_on['portfolio_cum_rets_on'] = (1+df_risk_on['portfolio_rets_on']).cumprod()-1
off_max = df_risk_off['portfolio_cum_rets_off'].max()
off_max

2.1271558415614313

In [87]:
df_risk_off[df_risk_off['portfolio_cum_rets_off'] == off_max]

XLP       XLU      XLV  portfolio_rets_off  \
Date                                                         
2020-02-18 -0.00355  0.008382 -0.00356            0.000424   

            portfolio_cum_rets_off  
Date                                
2020-02-18                2.127156

In [88]:
df_risk_on['portfolio_cum_rets_on'].max()

2.9835549668633954

In [89]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Create a figure
fig = go.Figure()

# Add trace, x axis, y axis, mode = lines
fig.add_trace(go.Scatter(x=df_risk_off.index, y=df_risk_off['portfolio_cum_rets_off'] * 100, mode='lines',line=dict(color='royalblue',width=2), name='risk off'))
fig.add_trace(go.Scatter(x=df_risk_on.index, y=df_risk_on['portfolio_cum_rets_on'] *100, mode='lines',line=dict(color='red',width=2), name='risk on'))


# Update Layout
fig.update_layout(
    title={'text':'Cumulative Performance',
           'y':0.9,
        'x':0.5,
          'xanchor': 'center',
             'yanchor': 'top' },
    
    xaxis=dict(
        title='',
        #ticksuffix="%",
        #tickprefix=''
    ),
    
    yaxis=dict(
        title='Returns',
         ticksuffix="%"
    ),
    
 
    paper_bgcolor='rgba(0,0,0,0)',
    plot_bgcolor='rgba(0,0,0,0)',
)


In [90]:
df_optimal = yf.download(['^GSPC','^VIX'],start='1998-12-02',end='2020-07-30')['Close']
df_optimal.head()

[*********************100%***********************]  2 of 2 completed


^GSPC       ^VIX
Date                              
1998-12-02  1171.250000  25.430000
1998-12-03  1150.140015  28.700001
1998-12-04  1176.739990  25.309999
1998-12-07  1187.699951  24.900000
1998-12-08  1181.380005  25.580000

In [91]:
df_optimal['GSPC rets'] = df_optimal['^GSPC'].pct_change()
df_optimal['VIX rets'] =  df_optimal['^VIX'].pct_change()
df_optimal

^GSPC       ^VIX  GSPC rets  VIX rets
Date                                                   
1998-12-02  1171.250000  25.430000        NaN       NaN
1998-12-03  1150.140015  28.700001  -0.018023  0.128588
1998-12-04  1176.739990  25.309999   0.023128 -0.118119
1998-12-07  1187.699951  24.900000   0.009314 -0.016199
1998-12-08  1181.380005  25.580000  -0.005321  0.027309
...                 ...        ...        ...       ...
2020-07-23  3235.659912  26.080000  -0.012320  0.072368
2020-07-24  3215.629883  25.840000  -0.006190 -0.009202
2020-07-27  3239.409912  24.740000   0.007395 -0.042570
2020-07-28  3218.439941  25.440001  -0.006473  0.028294
2020-07-29  3258.439941  24.100000   0.012428 -0.052673

[5449 rows x 4 columns]

In [92]:
df_optimal['real std'] = np.sqrt(252)*df_optimal['GSPC rets'].rolling(window=21,min_periods=1).std()
df_optimal['1mback VIX'] = df_optimal['^VIX'].shift(21)
df_optimal = df_optimal.dropna()
df_optimal

^GSPC       ^VIX  GSPC rets  VIX rets  real std  1mback VIX
Date                                                                         
1999-01-04  1228.099976  26.170000  -0.000919  0.071663  0.196405   25.430000
1999-01-05  1244.780029  24.459999   0.013582 -0.065342  0.185336   28.700001
1999-01-06  1272.339966  23.340000   0.022140 -0.045789  0.184069   25.309999
1999-01-07  1269.729980  24.370001  -0.002051  0.044130  0.183982   24.900000
1999-01-08  1275.089966  23.280001   0.004221 -0.044727  0.181331   25.580000
...                 ...        ...        ...       ...       ...         ...
2020-07-23  3235.659912  26.080000  -0.012320  0.072368  0.195012   31.370001
2020-07-24  3215.629883  25.840000  -0.006190 -0.009202  0.170433   33.840000
2020-07-27  3239.409912  24.740000   0.007395 -0.042570  0.168660   32.220001
2020-07-28  3218.439941  25.440001  -0.006473  0.028294  0.142532   34.730000
2020-07-29  3258.439941  24.100000   0.012428 -0.052673  0.140448   31.780001

[5428 rows x 6 columns]

In [93]:
df_optimal['equity allocation'] = np.where(100*df_optimal['real std'] < df_optimal['1mback VIX']+2,1,0)
df_optimal.tail()

<ipython-input-93-b9ff3c50a8eb>:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



^GSPC       ^VIX  GSPC rets  VIX rets  real std  1mback VIX  \
Date                                                                            
2020-07-23  3235.659912  26.080000  -0.012320  0.072368  0.195012   31.370001   
2020-07-24  3215.629883  25.840000  -0.006190 -0.009202  0.170433   33.840000   
2020-07-27  3239.409912  24.740000   0.007395 -0.042570  0.168660   32.220001   
2020-07-28  3218.439941  25.440001  -0.006473  0.028294  0.142532   34.730000   
2020-07-29  3258.439941  24.100000   0.012428 -0.052673  0.140448   31.780001   

            equity allocation  
Date                           
2020-07-23                  1  
2020-07-24                  1  
2020-07-27                  1  
2020-07-28                  1  
2020-07-29                  1

In [94]:
df_optimal['volatility allocation'] = 1 - df_optimal['equity allocation']
df_optimal

<ipython-input-94-dc58f3eba2bf>:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



^GSPC       ^VIX  GSPC rets  VIX rets  real std  1mback VIX  \
Date                                                                            
1999-01-04  1228.099976  26.170000  -0.000919  0.071663  0.196405   25.430000   
1999-01-05  1244.780029  24.459999   0.013582 -0.065342  0.185336   28.700001   
1999-01-06  1272.339966  23.340000   0.022140 -0.045789  0.184069   25.309999   
1999-01-07  1269.729980  24.370001  -0.002051  0.044130  0.183982   24.900000   
1999-01-08  1275.089966  23.280001   0.004221 -0.044727  0.181331   25.580000   
...                 ...        ...        ...       ...       ...         ...   
2020-07-23  3235.659912  26.080000  -0.012320  0.072368  0.195012   31.370001   
2020-07-24  3215.629883  25.840000  -0.006190 -0.009202  0.170433   33.840000   
2020-07-27  3239.409912  24.740000   0.007395 -0.042570  0.168660   32.220001   
2020-07-28  3218.439941  25.440001  -0.006473  0.028294  0.142532   34.730000   
2020-07-29  3258.439941  24.100000   0.012428 -0.052673  0.140448   31.780001   

            equity allocation  volatility allocation  
Date                                                  
1999-01-04                  1                      0  
1999-01-05                  1                      0  
1999-01-06                  1                      0  
1999-01-07                  1                      0  
1999-01-08                  1                      0  
...                       ...                    ...  
2020-07-23                  1                      0  
2020-07-24                  1                      0  
2020-07-27                  1                      0  
2020-07-28                  1                      0  
2020-07-29                  1                      0  

[5428 rows x 8 columns]

In [95]:
df_optimal['portfolio_rets_1'] = df_optimal['equity allocation']*df_risk_on['portfolio_rets_on'] + df_optimal['volatility allocation']*df_risk_off['portfolio_rets_off']
df_optimal

<ipython-input-95-84470265ce34>:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



^GSPC       ^VIX  GSPC rets  VIX rets  real std  1mback VIX  \
Date                                                                            
1999-01-04  1228.099976  26.170000  -0.000919  0.071663  0.196405   25.430000   
1999-01-05  1244.780029  24.459999   0.013582 -0.065342  0.185336   28.700001   
1999-01-06  1272.339966  23.340000   0.022140 -0.045789  0.184069   25.309999   
1999-01-07  1269.729980  24.370001  -0.002051  0.044130  0.183982   24.900000   
1999-01-08  1275.089966  23.280001   0.004221 -0.044727  0.181331   25.580000   
...                 ...        ...        ...       ...       ...         ...   
2020-07-23  3235.659912  26.080000  -0.012320  0.072368  0.195012   31.370001   
2020-07-24  3215.629883  25.840000  -0.006190 -0.009202  0.170433   33.840000   
2020-07-27  3239.409912  24.740000   0.007395 -0.042570  0.168660   32.220001   
2020-07-28  3218.439941  25.440001  -0.006473  0.028294  0.142532   34.730000   
2020-07-29  3258.439941  24.100000   0.012428 -0.052673  0.140448   31.780001   

            equity allocation  volatility allocation  portfolio_rets_1  
Date                                                                    
1999-01-04                  1                      0          0.000000  
1999-01-05                  1                      0          0.021898  
1999-01-06                  1                      0          0.024262  
1999-01-07                  1                      0         -0.005141  
1999-01-08                  1                      0          0.011715  
...                       ...                    ...               ...  
2020-07-23                  1                      0         -0.011768  
2020-07-24                  1                      0         -0.005438  
2020-07-27                  1                      0          0.010158  
2020-07-28                  1                      0         -0.012624  
2020-07-29                  1                      0          0.012012  

[5428 rows x 9 columns]

In [96]:
df_optimal['portfolio_cum_rets_1'] = (df_optimal['portfolio_rets_1']+1).cumprod()-1
df_optimal['GSPC_cum_rets'] = (df_optimal['GSPC rets']+1).cumprod()-1
df_optimal

<ipython-input-96-48e688cd7760>:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

<ipython-input-96-48e688cd7760>:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



^GSPC       ^VIX  GSPC rets  VIX rets  real std  1mback VIX  \
Date                                                                            
1999-01-04  1228.099976  26.170000  -0.000919  0.071663  0.196405   25.430000   
1999-01-05  1244.780029  24.459999   0.013582 -0.065342  0.185336   28.700001   
1999-01-06  1272.339966  23.340000   0.022140 -0.045789  0.184069   25.309999   
1999-01-07  1269.729980  24.370001  -0.002051  0.044130  0.183982   24.900000   
1999-01-08  1275.089966  23.280001   0.004221 -0.044727  0.181331   25.580000   
...                 ...        ...        ...       ...       ...         ...   
2020-07-23  3235.659912  26.080000  -0.012320  0.072368  0.195012   31.370001   
2020-07-24  3215.629883  25.840000  -0.006190 -0.009202  0.170433   33.840000   
2020-07-27  3239.409912  24.740000   0.007395 -0.042570  0.168660   32.220001   
2020-07-28  3218.439941  25.440001  -0.006473  0.028294  0.142532   34.730000   
2020-07-29  3258.439941  24.100000   0.012428 -0.052673  0.140448   31.780001   

            equity allocation  volatility allocation  portfolio_rets_1  \
Date                                                                     
1999-01-04                  1                      0          0.000000   
1999-01-05                  1                      0          0.021898   
1999-01-06                  1                      0          0.024262   
1999-01-07                  1                      0         -0.005141   
1999-01-08                  1                      0          0.011715   
...                       ...                    ...               ...   
2020-07-23                  1                      0         -0.011768   
2020-07-24                  1                      0         -0.005438   
2020-07-27                  1                      0          0.010158   
2020-07-28                  1                      0         -0.012624   
2020-07-29                  1                      0          0.012012   

            portfolio_cum_rets_1  GSPC_cum_rets  
Date                                             
1999-01-04              0.000000      -0.000919  
1999-01-05              0.021898       0.012650  
1999-01-06              0.046691       0.035071  
1999-01-07              0.041310       0.032947  
1999-01-08              0.053509       0.037308  
...                          ...            ...  
2020-07-23              3.876889       1.632266  
2020-07-24              3.850367       1.615971  
2020-07-27              3.899636       1.635316  
2020-07-28              3.837782       1.618257  
2020-07-29              3.895892       1.650798  

[5428 rows x 11 columns]

In [97]:
df_optimal['portfolio_cum_rets_1'].max()

3.934965081686734

In [98]:
df_optimal['GSPC_cum_rets'].max()

1.7546919259587743

In [99]:
fig = go.Figure()

# Add trace, x axis, y axis, mode = lines
fig.add_trace(go.Scatter(x=df_optimal.index, y=df_optimal['GSPC_cum_rets'] * 100, mode='lines',line=dict(color='royalblue',width=2), name='SPY'))
fig.add_trace(go.Scatter(x=df_optimal.index, y=df_optimal['portfolio_cum_rets_1'] *100, mode='lines',line=dict(color='red',width=2), name='Portfolio_1'))


# Update Layout
fig.update_layout(
    title={'text':'Cumulative Performance',
           'y':0.9,
        'x':0.5,
          'xanchor': 'center',
             'yanchor': 'top' },
    
    xaxis=dict(
        title='',
        #ticksuffix="%",
        #tickprefix=''
    ),
    
    yaxis=dict(
        title='Returns',
         ticksuffix="%"
    ),
    
 
    paper_bgcolor='rgba(0,0,0,0)',
    plot_bgcolor='rgba(0,0,0,0)',
)


In [100]:
df_optimal['GLD'] = yf.download(['GLD'],start='1998-12-02',end='2020-07-30')['Close']
df_optimal['GLD_rets'] = df_optimal['GLD'].pct_change()
df_optimal['GLD_cum_rets'] = (1+df_optimal['GLD_rets']).cumprod()-1
df_optimal[['Risk_rets_on','Risk_cum_rets_on']] = df_risk_on[['portfolio_rets_on','portfolio_cum_rets_on']]
df_optimal[['Risk_rets_off','Risk_cum_rets_off']] = df_risk_off[['portfolio_rets_off','portfolio_cum_rets_off']]
df_optimal

[*********************100%***********************]  1 of 1 completed


<ipython-input-100-1ebdb3d9e027>:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

<ipython-input-100-1ebdb3d9e027>:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

<ipython-input-100-1ebdb3d9e027>:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

D:\anaconda3\lib\site-

^GSPC       ^VIX  GSPC rets  VIX rets  real std  1mback VIX  \
Date                                                                            
1999-01-04  1228.099976  26.170000  -0.000919  0.071663  0.196405   25.430000   
1999-01-05  1244.780029  24.459999   0.013582 -0.065342  0.185336   28.700001   
1999-01-06  1272.339966  23.340000   0.022140 -0.045789  0.184069   25.309999   
1999-01-07  1269.729980  24.370001  -0.002051  0.044130  0.183982   24.900000   
1999-01-08  1275.089966  23.280001   0.004221 -0.044727  0.181331   25.580000   
...                 ...        ...        ...       ...       ...         ...   
2020-07-23  3235.659912  26.080000  -0.012320  0.072368  0.195012   31.370001   
2020-07-24  3215.629883  25.840000  -0.006190 -0.009202  0.170433   33.840000   
2020-07-27  3239.409912  24.740000   0.007395 -0.042570  0.168660   32.220001   
2020-07-28  3218.439941  25.440001  -0.006473  0.028294  0.142532   34.730000   
2020-07-29  3258.439941  24.100000   0.012428 -0.052673  0.140448   31.780001   

            equity allocation  volatility allocation  portfolio_rets_1  \
Date                                                                     
1999-01-04                  1                      0          0.000000   
1999-01-05                  1                      0          0.021898   
1999-01-06                  1                      0          0.024262   
1999-01-07                  1                      0         -0.005141   
1999-01-08                  1                      0          0.011715   
...                       ...                    ...               ...   
2020-07-23                  1                      0         -0.011768   
2020-07-24                  1                      0         -0.005438   
2020-07-27                  1                      0          0.010158   
2020-07-28                  1                      0         -0.012624   
2020-07-29                  1                      0          0.012012   

            portfolio_cum_rets_1  GSPC_cum_rets         GLD  GLD_rets  \
Date                                                                    
1999-01-04              0.000000      -0.000919         NaN       NaN   
1999-01-05              0.021898       0.012650         NaN       NaN   
1999-01-06              0.046691       0.035071         NaN       NaN   
1999-01-07              0.041310       0.032947         NaN       NaN   
1999-01-08              0.053509       0.037308         NaN       NaN   
...                          ...            ...         ...       ...   
2020-07-23              3.876889       1.632266  177.179993  0.008825   
2020-07-24              3.850367       1.615971  178.699997  0.008579   
2020-07-27              3.899636       1.635316  182.229996  0.019754   
2020-07-28              3.837782       1.618257  183.750000  0.008341   
2020-07-29              3.895892       1.650798  185.130005  0.007510   

            GLD_cum_rets  Risk_rets_on  Risk_cum_rets_on  Risk_rets_off  \
Date                                                                      
1999-01-04           NaN      0.000000          0.000000       0.000000   
1999-01-05           NaN      0.021898          0.021898       0.011761   
1999-01-06           NaN      0.024262          0.046691       0.013025   
1999-01-07           NaN     -0.005141          0.041310      -0.006546   
1999-01-08           NaN      0.011715          0.053509       0.004651   
...                  ...           ...               ...            ...   
2020-07-23      2.992339     -0.011768          2.923038       0.000069   
2020-07-24      3.026588     -0.005438          2.901703      -0.006296   
2020-07-27      3.106129      0.010158          2.941336       0.000132   
2020-07-28      3.140378     -0.012624          2.891580       0.005888   
2020-07-29      3.171474      0.012012          2.938324       0.005521   

            Risk_cum_rets_off  
Date                           
1999-01-04 

In [101]:
#same volatility strategy but for risk on and gold
#在实际std大于VIX预测值时，证明市场波动大，我们买入黄金因其具有稳定的金融特质，我们基本不会产生过多亏损。
#详情可以参考我们在mini_project中分时间段对黄金以及大盘的走势分析
#可以清晰的看到黄金的稳定特质
df_optimal['portfolio_rets_2'] = df_optimal['equity allocation']*df_risk_on['portfolio_rets_on'] + df_optimal['volatility allocation']*df_optimal['GLD_rets']
df_optimal

<ipython-input-101-a303d1d886b4>:5: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



^GSPC       ^VIX  GSPC rets  VIX rets  real std  1mback VIX  \
Date                                                                            
1999-01-04  1228.099976  26.170000  -0.000919  0.071663  0.196405   25.430000   
1999-01-05  1244.780029  24.459999   0.013582 -0.065342  0.185336   28.700001   
1999-01-06  1272.339966  23.340000   0.022140 -0.045789  0.184069   25.309999   
1999-01-07  1269.729980  24.370001  -0.002051  0.044130  0.183982   24.900000   
1999-01-08  1275.089966  23.280001   0.004221 -0.044727  0.181331   25.580000   
...                 ...        ...        ...       ...       ...         ...   
2020-07-23  3235.659912  26.080000  -0.012320  0.072368  0.195012   31.370001   
2020-07-24  3215.629883  25.840000  -0.006190 -0.009202  0.170433   33.840000   
2020-07-27  3239.409912  24.740000   0.007395 -0.042570  0.168660   32.220001   
2020-07-28  3218.439941  25.440001  -0.006473  0.028294  0.142532   34.730000   
2020-07-29  3258.439941  24.100000   0.012428 -0.052673  0.140448   31.780001   

            equity allocation  volatility allocation  portfolio_rets_1  \
Date                                                                     
1999-01-04                  1                      0          0.000000   
1999-01-05                  1                      0          0.021898   
1999-01-06                  1                      0          0.024262   
1999-01-07                  1                      0         -0.005141   
1999-01-08                  1                      0          0.011715   
...                       ...                    ...               ...   
2020-07-23                  1                      0         -0.011768   
2020-07-24                  1                      0         -0.005438   
2020-07-27                  1                      0          0.010158   
2020-07-28                  1                      0         -0.012624   
2020-07-29                  1                      0          0.012012   

            portfolio_cum_rets_1  GSPC_cum_rets         GLD  GLD_rets  \
Date                                                                    
1999-01-04              0.000000      -0.000919         NaN       NaN   
1999-01-05              0.021898       0.012650         NaN       NaN   
1999-01-06              0.046691       0.035071         NaN       NaN   
1999-01-07              0.041310       0.032947         NaN       NaN   
1999-01-08              0.053509       0.037308         NaN       NaN   
...                          ...            ...         ...       ...   
2020-07-23              3.876889       1.632266  177.179993  0.008825   
2020-07-24              3.850367       1.615971  178.699997  0.008579   
2020-07-27              3.899636       1.635316  182.229996  0.019754   
2020-07-28              3.837782       1.618257  183.750000  0.008341   
2020-07-29              3.895892       1.650798  185.130005  0.007510   

            GLD_cum_rets  Risk_rets_on  Risk_cum_rets_on  Risk_rets_off  \
Date                                                                      
1999-01-04           NaN      0.000000          0.000000       0.000000   
1999-01-05           NaN      0.021898          0.021898       0.011761   
1999-01-06           NaN      0.024262          0.046691       0.013025   
1999-01-07           NaN     -0.005141          0.041310      -0.006546   
1999-01-08           NaN      0.011715          0.053509       0.004651   
...                  ...           ...               ...            ...   
2020-07-23      2.992339     -0.011768          2.923038       0.000069   
2020-07-24      3.026588     -0.005438          2.901703      -0.006296   
2020-07-27      3.106129      0.010158          2.941336       0.000132   
2020-07-28      3.140378     -0.012624          2.891580       0.005888   
2020-07-29      3.171474      0.012012          2.938324       0.005521   

            Risk_cum_rets_off  portfolio_rets_2  
Date                     

In [102]:
df_optimal['portfolio_cum_rets_2'] = (1+df_optimal['portfolio_rets_2']).cumprod()-1
df_optimal

<ipython-input-102-3b2f34ec1c49>:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



^GSPC       ^VIX  GSPC rets  VIX rets  real std  1mback VIX  \
Date                                                                            
1999-01-04  1228.099976  26.170000  -0.000919  0.071663  0.196405   25.430000   
1999-01-05  1244.780029  24.459999   0.013582 -0.065342  0.185336   28.700001   
1999-01-06  1272.339966  23.340000   0.022140 -0.045789  0.184069   25.309999   
1999-01-07  1269.729980  24.370001  -0.002051  0.044130  0.183982   24.900000   
1999-01-08  1275.089966  23.280001   0.004221 -0.044727  0.181331   25.580000   
...                 ...        ...        ...       ...       ...         ...   
2020-07-23  3235.659912  26.080000  -0.012320  0.072368  0.195012   31.370001   
2020-07-24  3215.629883  25.840000  -0.006190 -0.009202  0.170433   33.840000   
2020-07-27  3239.409912  24.740000   0.007395 -0.042570  0.168660   32.220001   
2020-07-28  3218.439941  25.440001  -0.006473  0.028294  0.142532   34.730000   
2020-07-29  3258.439941  24.100000   0.012428 -0.052673  0.140448   31.780001   

            equity allocation  volatility allocation  portfolio_rets_1  \
Date                                                                     
1999-01-04                  1                      0          0.000000   
1999-01-05                  1                      0          0.021898   
1999-01-06                  1                      0          0.024262   
1999-01-07                  1                      0         -0.005141   
1999-01-08                  1                      0          0.011715   
...                       ...                    ...               ...   
2020-07-23                  1                      0         -0.011768   
2020-07-24                  1                      0         -0.005438   
2020-07-27                  1                      0          0.010158   
2020-07-28                  1                      0         -0.012624   
2020-07-29                  1                      0          0.012012   

            portfolio_cum_rets_1  GSPC_cum_rets         GLD  GLD_rets  \
Date                                                                    
1999-01-04              0.000000      -0.000919         NaN       NaN   
1999-01-05              0.021898       0.012650         NaN       NaN   
1999-01-06              0.046691       0.035071         NaN       NaN   
1999-01-07              0.041310       0.032947         NaN       NaN   
1999-01-08              0.053509       0.037308         NaN       NaN   
...                          ...            ...         ...       ...   
2020-07-23              3.876889       1.632266  177.179993  0.008825   
2020-07-24              3.850367       1.615971  178.699997  0.008579   
2020-07-27              3.899636       1.635316  182.229996  0.019754   
2020-07-28              3.837782       1.618257  183.750000  0.008341   
2020-07-29              3.895892       1.650798  185.130005  0.007510   

            GLD_cum_rets  Risk_rets_on  Risk_cum_rets_on  Risk_rets_off  \
Date                                                                      
1999-01-04           NaN      0.000000          0.000000       0.000000   
1999-01-05           NaN      0.021898          0.021898       0.011761   
1999-01-06           NaN      0.024262          0.046691       0.013025   
1999-01-07           NaN     -0.005141          0.041310      -0.006546   
1999-01-08           NaN      0.011715          0.053509       0.004651   
...                  ...           ...               ...            ...   
2020-07-23      2.992339     -0.011768          2.923038       0.000069   
2020-07-24      3.026588     -0.005438          2.901703      -0.006296   
2020-07-27      3.106129      0.010158          2.941336       0.000132   
2020-07-28      3.140378     -0.012624          2.891580       0.005888   
2020-07-29      3.171474      0.012012          2.938324       0.005521   

            Risk_cum_rets_off  portfolio_rets_2  portfolio_cum_rets_2  
Dat

In [131]:
# We can see the GLD and risk on has far more cum-rets than risk on and off



fig = go.Figure()

# Add trace, x axis, y axis, mode = lines
fig.add_trace(go.Scatter(x=df_optimal.index, y=df_optimal['GSPC_cum_rets'] * 100, mode='lines',line=dict(color='royalblue',width=2), name='SPY'))
fig.add_trace(go.Scatter(x=df_optimal.index, y=df_optimal['portfolio_cum_rets_2'] *100, mode='lines',line=dict(color='red',width=2), name='Portfolio_2'))


# Update Layout
fig.update_layout(
    title={'text':'Cumulative Performance',
           'y':0.9,
        'x':0.5,
          'xanchor': 'center',
             'yanchor': 'top' },
    
    xaxis=dict(
        title='',
        #ticksuffix="%",
        #tickprefix=''
    ),
    
    yaxis=dict(
        title='Returns',
         ticksuffix="%"
    ),
    
 
    paper_bgcolor='rgba(0,0,0,0)',
    plot_bgcolor='rgba(0,0,0,0)',
)

In [104]:
df_portfolio = df_optimal[['portfolio_rets_2','portfolio_cum_rets_2']].dropna()
df_portfolio

portfolio_rets_2  portfolio_cum_rets_2
Date                                              
2004-11-19         -0.011737             -0.011737
2004-11-22          0.005426             -0.006375
2004-11-23         -0.001277             -0.007643
2004-11-24          0.007267             -0.000432
2004-11-26          0.002400              0.001967
...                      ...                   ...
2020-07-23         -0.011768              5.786763
2020-07-24         -0.005438              5.749854
2020-07-27          0.010158              5.818418
2020-07-28         -0.012624              5.732341
2020-07-29          0.012012              5.813207

[3949 rows x 2 columns]

In [105]:
n = len(df_portfolio)
Port_Ann_Ret = 100* ( (1+df_portfolio["portfolio_cum_rets_2"][-1])**(252/n) - 1 )
print('Portfolio Annualized Return: ',np.round(Port_Ann_Ret,2),'%')

Port_ann_vol = np.sqrt(252)*df_portfolio['portfolio_rets_2'].std()
print("Portfolio Annualized Volatility: ", np.round(100*Port_ann_vol,2),"%")

sharpe_ratio = (Port_Ann_Ret/100)/Port_ann_vol
print("Strategy SR: ", np.round(sharpe_ratio,2))

Portfolio Annualized Return:  13.03 %
Portfolio Annualized Volatility:  17.96 %
Strategy SR:  0.73


In [107]:
n = len(df_optimal)
Port_Ann_Ret = 100* ( (1+df_optimal["portfolio_cum_rets_1"][-1])**(252/n) - 1 )
print('Portfolio Annualized Return: ',np.round(Port_Ann_Ret,2),'%')

Port_ann_vol = np.sqrt(252)*df_optimal['portfolio_rets_1'].std()
print("Portfolio Annualized Volatility: ", np.round(100*Port_ann_vol,2),"%")

sharpe_ratio = (Port_Ann_Ret/100)/Port_ann_vol
print("Strategy SR: ", np.round(sharpe_ratio,2))

Portfolio Annualized Return:  7.65 %
Portfolio Annualized Volatility:  19.32 %
Strategy SR:  0.4


In [108]:
n = len(df_optimal)
SPY_Ann_Ret = 100* ( (1+df_optimal["GSPC_cum_rets"][-1])**(252/n) - 1 )
SPY_ann_vol = np.sqrt(252)*df_optimal['GSPC rets'].std()


print('\n\nSPY Annualized Return: ',np.round(SPY_Ann_Ret,2),'%')
print("SPY Annualized Volatility: ", np.round(100*SPY_ann_vol,2),"%")

sharpe_ratio_SPY = (SPY_Ann_Ret/100)/SPY_ann_vol
print("SPY SR: ",np.round(sharpe_ratio_SPY,2))



SPY Annualized Return:  4.63 %
SPY Annualized Volatility:  19.86 %
SPY SR:  0.23


In [109]:
df_optimal

^GSPC       ^VIX  GSPC rets  VIX rets  real std  1mback VIX  \
Date                                                                            
1999-01-04  1228.099976  26.170000  -0.000919  0.071663  0.196405   25.430000   
1999-01-05  1244.780029  24.459999   0.013582 -0.065342  0.185336   28.700001   
1999-01-06  1272.339966  23.340000   0.022140 -0.045789  0.184069   25.309999   
1999-01-07  1269.729980  24.370001  -0.002051  0.044130  0.183982   24.900000   
1999-01-08  1275.089966  23.280001   0.004221 -0.044727  0.181331   25.580000   
...                 ...        ...        ...       ...       ...         ...   
2020-07-23  3235.659912  26.080000  -0.012320  0.072368  0.195012   31.370001   
2020-07-24  3215.629883  25.840000  -0.006190 -0.009202  0.170433   33.840000   
2020-07-27  3239.409912  24.740000   0.007395 -0.042570  0.168660   32.220001   
2020-07-28  3218.439941  25.440001  -0.006473  0.028294  0.142532   34.730000   
2020-07-29  3258.439941  24.100000   0.012428 -0.052673  0.140448   31.780001   

            equity allocation  volatility allocation  portfolio_rets_1  \
Date                                                                     
1999-01-04                  1                      0          0.000000   
1999-01-05                  1                      0          0.021898   
1999-01-06                  1                      0          0.024262   
1999-01-07                  1                      0         -0.005141   
1999-01-08                  1                      0          0.011715   
...                       ...                    ...               ...   
2020-07-23                  1                      0         -0.011768   
2020-07-24                  1                      0         -0.005438   
2020-07-27                  1                      0          0.010158   
2020-07-28                  1                      0         -0.012624   
2020-07-29                  1                      0          0.012012   

            portfolio_cum_rets_1  GSPC_cum_rets         GLD  GLD_rets  \
Date                                                                    
1999-01-04              0.000000      -0.000919         NaN       NaN   
1999-01-05              0.021898       0.012650         NaN       NaN   
1999-01-06              0.046691       0.035071         NaN       NaN   
1999-01-07              0.041310       0.032947         NaN       NaN   
1999-01-08              0.053509       0.037308         NaN       NaN   
...                          ...            ...         ...       ...   
2020-07-23              3.876889       1.632266  177.179993  0.008825   
2020-07-24              3.850367       1.615971  178.699997  0.008579   
2020-07-27              3.899636       1.635316  182.229996  0.019754   
2020-07-28              3.837782       1.618257  183.750000  0.008341   
2020-07-29              3.895892       1.650798  185.130005  0.007510   

            GLD_cum_rets  Risk_rets_on  Risk_cum_rets_on  Risk_rets_off  \
Date                                                                      
1999-01-04           NaN      0.000000          0.000000       0.000000   
1999-01-05           NaN      0.021898          0.021898       0.011761   
1999-01-06           NaN      0.024262          0.046691       0.013025   
1999-01-07           NaN     -0.005141          0.041310      -0.006546   
1999-01-08           NaN      0.011715          0.053509       0.004651   
...                  ...           ...               ...            ...   
2020-07-23      2.992339     -0.011768          2.923038       0.000069   
2020-07-24      3.026588     -0.005438          2.901703      -0.006296   
2020-07-27      3.106129      0.010158          2.941336       0.000132   
2020-07-28      3.140378     -0.012624          2.891580       0.005888   
2020-07-29      3.171474      0.012012          2.938324       0.005521   

            Risk_cum_rets_off  portfolio_rets_2  portfolio_cum_rets_2  
Dat

In [110]:
#compute 95% and 99% VaR for portfolio 2
var_d95 = np.percentile(df_optimal['portfolio_rets_2'].dropna(),5)
print("The minimum daily loss" ,5,"% of the time is",var_d95,"%")
var_d95_GSPC = np.percentile(df_optimal['GSPC rets'].dropna(),5)
print("The minimum daily loss of SPY" ,5,"% of the time is",var_d95_GSPC,"%")

The minimum daily loss 5 % of the time is -0.018018807077118122 %
The minimum daily loss of SPY 5 % of the time is -0.01896197241721396 %


In [111]:
#Compute 99 VaR 
var_d99 = np.percentile (df_optimal['portfolio_rets_2'].dropna(),1)
print("The minimum daily loss" ,1,"% of the time is",var_d99,"%")
var_d99_GSPC = np.percentile(df_optimal['GSPC_cum_rets'].dropna(),1)
print("The minimum daily loss of SPY" ,1,"% of the time is",var_d99_GSPC,"%")

The minimum daily loss 1 % of the time is -0.032907501062990306 %
The minimum daily loss of SPY 1 % of the time is -0.3286564807506598 %


In [112]:
cvar = df_optimal[df_optimal['portfolio_rets_2'] <= var_d95]['portfolio_rets_2'].mean()
print('The CVaR',5,"% of the time is",cvar)
cvar_GSPC = df_optimal[df_optimal['GSPC rets'] <= var_d95_GSPC]['GSPC rets'].mean()
print('The CVaR of SPY',5,"% of the time is",cvar_GSPC)

The CVaR 5 % of the time is -0.02737242377393524
The CVaR of SPY 5 % of the time is -0.029974305584673205


In [113]:
window = 252
df_optimal['rolling_max'] = df_optimal['portfolio_cum_rets_2'].rolling(window, min_periods=1).max()
df_optimal['rolling_max_GSPC'] = df_optimal['^GSPC'].rolling(window, min_periods=1).max()

<ipython-input-113-dc739b0cb0c7>:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

<ipython-input-113-dc739b0cb0c7>:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [114]:
df_optimal['daily_drawdown'] = 1-(1+df_optimal['portfolio_cum_rets_2'])/(1+df_optimal['rolling_max'])
df_optimal['daily_drawdown_GSPC'] = (df_optimal['rolling_max_GSPC'] - df_optimal['^GSPC'])/df_optimal['rolling_max_GSPC']
df_optimal.tail()

<ipython-input-114-18315624e677>:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

<ipython-input-114-18315624e677>:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



^GSPC       ^VIX  GSPC rets  VIX rets  real std  1mback VIX  \
Date                                                                            
2020-07-23  3235.659912  26.080000  -0.012320  0.072368  0.195012   31.370001   
2020-07-24  3215.629883  25.840000  -0.006190 -0.009202  0.170433   33.840000   
2020-07-27  3239.409912  24.740000   0.007395 -0.042570  0.168660   32.220001   
2020-07-28  3218.439941  25.440001  -0.006473  0.028294  0.142532   34.730000   
2020-07-29  3258.439941  24.100000   0.012428 -0.052673  0.140448   31.780001   

            equity allocation  volatility allocation  portfolio_rets_1  \
Date                                                                     
2020-07-23                  1                      0         -0.011768   
2020-07-24                  1                      0         -0.005438   
2020-07-27                  1                      0          0.010158   
2020-07-28                  1                      0         -0.012624   
2020-07-29                  1                      0          0.012012   

            portfolio_cum_rets_1  ...  Risk_rets_on  Risk_cum_rets_on  \
Date                              ...                                   
2020-07-23              3.876889  ...     -0.011768          2.923038   
2020-07-24              3.850367  ...     -0.005438          2.901703   
2020-07-27              3.899636  ...      0.010158          2.941336   
2020-07-28              3.837782  ...     -0.012624          2.891580   
2020-07-29              3.895892  ...      0.012012          2.938324   

            Risk_rets_off  Risk_cum_rets_off  portfolio_rets_2  \
Date                                                             
2020-07-23       0.000069           1.969775         -0.011768   
2020-07-24      -0.006296           1.951077         -0.005438   
2020-07-27       0.000132           1.951467          0.010158   
2020-07-28       0.005888           1.968845         -0.012624   
2020-07-29       0.005521           1.985235          0.012012   

            portfolio_cum_rets_2  rolling_max  rolling_max_GSPC  \
Date                                                              
2020-07-23              5.786763     5.885902       3386.149902   
2020-07-24              5.749854     5.885902       3386.149902   
2020-07-27              5.818418     5.885902       3386.149902   
2020-07-28              5.732341     5.885902       3386.149902   
2020-07-29              5.813207     5.885902       3386.149902   

            daily_drawdown  daily_drawdown_GSPC  
Date                                             
2020-07-23        0.014397             0.044443  
2020-07-24        0.019757             0.050358  
2020-07-27        0.009800             0.043335  
2020-07-28        0.022301             0.049528  
2020-07-29        0.010557             0.037715  

[5 rows x 24 columns]

In [115]:
max_drawdown = df_optimal['daily_drawdown'].max()
print(max_drawdown)
max_drawdown_GSPC = df_optimal['daily_drawdown_GSPC'].max()
max_drawdown_GSPC

0.3526077534391524


0.5257845222788181

In [132]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Create a figure
fig = go.Figure()

# Add trace, x axis, y axis, mode = lines
fig.add_trace(go.Scatter(x=df_optimal.index, y=-df_optimal["daily_drawdown"]*100, mode='lines',line=dict(color='red',width=2), name='Portfolio'))
fig.add_trace(go.Scatter(x=df_optimal.index, y=-df_optimal["daily_drawdown_GSPC"]*100, mode='lines',line=dict(color='black',width=2), name='SPY'))



# Update Layout
fig.update_layout(
    title={'text':'Maximum Drawdown',
           'y':0.9,
        'x':0.5,
          'xanchor': 'center',
             'yanchor': 'top' },
    
    xaxis=dict(
        title='',
        #ticksuffix="%",
        #tickprefix=''
    ),
    
    yaxis=dict(
        title='',
         ticksuffix="%"
    ),
    
 
    paper_bgcolor='rgba(0,0,0,0)',
    plot_bgcolor='rgba(0,0,0,0)',
)

In [118]:
df_corr = df_risk_on[['portfolio_rets_on']]
df_corr['portfolio_rets_off'] = df_risk_off['portfolio_rets_off']
df_corr['GSPC_rets'] = df_optimal['GSPC rets']
df_corr

<ipython-input-118-dd1f838b3e62>:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

<ipython-input-118-dd1f838b3e62>:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



portfolio_rets_on  portfolio_rets_off  GSPC_rets
Date                                                        
1999-01-04           0.000000            0.000000  -0.000919
1999-01-05           0.021898            0.011761   0.013582
1999-01-06           0.024262            0.013025   0.022140
1999-01-07          -0.005141           -0.006546  -0.002051
1999-01-08           0.011715            0.004651   0.004221
...                       ...                 ...        ...
2020-07-23          -0.011768            0.000069  -0.012320
2020-07-24          -0.005438           -0.006296  -0.006190
2020-07-27           0.010158            0.000132   0.007395
2020-07-28          -0.012624            0.005888  -0.006473
2020-07-29           0.012012            0.005521   0.012428

[5428 rows x 3 columns]

In [119]:
df_corr.corr()

portfolio_rets_on  portfolio_rets_off  GSPC_rets
portfolio_rets_on            1.000000            0.776582   0.957195
portfolio_rets_off           0.776582            1.000000   0.842991
GSPC_rets                    0.957195            0.842991   1.000000

In [136]:
corr_matrix = df_corr.corr().values
# Round the numbers to 2 digits
corr_matrix = np.round(corr_matrix,2)
corr_matrix

array([[1.  , 0.78, 0.96],
       [0.78, 1.  , 0.84],
       [0.96, 0.84, 1.  ]])

In [138]:
import plotly.figure_factory as ff
z = corr_matrix
x = list(df_corr.columns)
y = list(df_corr.columns)
#r = [ ['La','va','nda],[1,2,3,4],[1,2,3,4]]



fig = ff.create_annotated_heatmap(z, x=x, y=y, annotation_text=z, colorscale='reds')
fig.update_layout(
    title={'text':'Correlation Map',
          'y':0.9,
          'x':0.5})
fig.show()


In [120]:
window = 180
corr_on = df_corr['portfolio_rets_on'].rolling(window).corr(df_corr['GSPC_rets'])
corr_off = df_corr['portfolio_rets_off'].rolling(window).corr(df_corr['GSPC_rets'])

In [133]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Create a figure
fig = make_subplots(rows=2,cols=1)

# Add trace, x axis, y axis, mode = lines
fig.add_trace(go.Scatter(x=df_corr.index, y=corr_off, mode='lines',line=dict(color='red',width=2), name='Risk off sector'),row=1,col=1)
fig.add_trace(go.Scatter(x=df_corr.index, y=corr_on, mode='lines',line=dict(color='black',width=2), name='Risk on sector'),row=1,col=1)
fig.add_trace(go.Scatter(x=df_corr.index, y=df_optimal['GSPC_cum_rets'], mode='lines',line=dict(color='blue',width=2), name='SPY'),row=2,col=1)
fig.add_trace(go.Scatter(x=df_corr.index, y=df_optimal['Risk_cum_rets_off'], mode='lines',line=dict(color='black',width=2), name='Risk off sector'),row=2,col=1)


# Update Layout
fig.update_layout(
    title={'text':'Correlation of Each ETFs sector with SPY',
           'y':0.9,
        'x':0.5,
          'xanchor': 'center',
             'yanchor': 'top' },
    
    xaxis=dict(
        title='',
        #ticksuffix="%",
        #tickprefix=''
    ),
    
    yaxis=dict(
        title='Correlation',
         ticksuffix=""
    ),
    
 
    paper_bgcolor='rgba(0,0,0,0)',
    plot_bgcolor='rgba(0,0,0,0)',
)

In [122]:
# Actually the correlation of risk on ETFs sector is more stabler than risk off sector

In [41]:
import statsmodels.api as sm
X = df_corr['GSPC_rets']
X = sm.add_constant(X)
Y = df_corr['portfolio_rets_on']
model_on = sm.OLS(Y,X, missing='drop').fit()
model_on.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:      portfolio_rets_on   R-squared:                       0.916
Model:                            OLS   Adj. R-squared:                  0.916
Method:                 Least Squares   F-statistic:                 5.934e+04
Date:                Fri, 18 Sep 2020   Prob (F-statistic):               0.00
Time:                        18:27:20   Log-Likelihood:                 22420.
No. Observations:                5428   AIC:                        -4.484e+04
Df Residuals:                    5426   BIC:                        -4.482e+04
Df Model:                           1                                         
Covariance Type:            nonrobust                                         
==============================================================================
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
const       7.773e-05   5.28e-05      1.472      0.141   -2.58e-05       0.000
GSPC_rets      1.0281      0.004    243.601      0.000       1.020       1.036
==============================================================================
Omnibus:                      765.309   Durbin-Watson:                   2.081
Prob(Omnibus):                  0.000   Jarque-Bera (JB):            10324.238
Skew:                           0.139   Prob(JB):                         0.00
Kurtosis:                       9.751   Cond. No.                         79.9
==============================================================================

Warnings:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

In [42]:
Z = df_corr['portfolio_rets_off']
model_off = sm.OLS(Z,X,missing='drop').fit()
model_off.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:     portfolio_rets_off   R-squared:                       0.711
Model:                            OLS   Adj. R-squared:                  0.711
Method:                 Least Squares   F-statistic:                 1.333e+04
Date:                Fri, 18 Sep 2020   Prob (F-statistic):               0.00
Time:                        18:27:20   Log-Likelihood:                 20851.
No. Observations:                5428   AIC:                        -4.170e+04
Df Residuals:                    5426   BIC:                        -4.169e+04
Df Model:                           1                                         
Covariance Type:            nonrobust                                         
==============================================================================
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
const       8.028e-05   7.05e-05      1.138      0.255    -5.8e-05       0.000
GSPC_rets      0.6505      0.006    115.435      0.000       0.639       0.662
==============================================================================
Omnibus:                      684.497   Durbin-Watson:                   2.060
Prob(Omnibus):                  0.000   Jarque-Bera (JB):             7956.986
Skew:                          -0.032   Prob(JB):                         0.00
Kurtosis:                       8.931   Cond. No.                         79.9
==============================================================================

Warnings:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

In [43]:
#Yes risk on sector has higher risk than risk off sector

In [44]:
df_risk_off

XLP       XLU       XLV  portfolio_rets_off  \
Date                                                           
1999-01-04       NaN       NaN       NaN            0.000000   
1999-01-05  0.007541  0.012080  0.015663            0.011761   
1999-01-06  0.012090  0.010379  0.016607            0.013025   
1999-01-07 -0.011377 -0.003595 -0.004667           -0.006546   
1999-01-08 -0.004028  0.005670  0.012309            0.004651   
...              ...       ...       ...                 ...   
2020-07-23  0.003549  0.001155 -0.004497            0.000069   
2020-07-24 -0.001286 -0.006592 -0.011010           -0.006296   
2020-07-27  0.004989 -0.012110  0.007517            0.000132   
2020-07-28  0.003684  0.015113 -0.001133            0.005888   
2020-07-29  0.001436  0.004632  0.010494            0.005521   

            portfolio_cum_rets_off  
Date                                
1999-01-04                0.000000  
1999-01-05                0.011761  
1999-01-06                0.024940  
1999-01-07                0.018230  
1999-01-08                0.022965  
...                            ...  
2020-07-23                1.969775  
2020-07-24                1.951077  
2020-07-27                1.951467  
2020-07-28                1.968845  
2020-07-29                1.985235  

[5428 rows x 5 columns]

In [45]:
df_optimal

^GSPC       ^VIX  GSPC rets  VIX rets  real std  1mback VIX  \
Date                                                                            
1999-01-04  1228.099976  26.170000  -0.000919  0.071663  0.196405   25.430000   
1999-01-05  1244.780029  24.459999   0.013582 -0.065342  0.185336   28.700001   
1999-01-06  1272.339966  23.340000   0.022140 -0.045789  0.184069   25.309999   
1999-01-07  1269.729980  24.370001  -0.002051  0.044130  0.183982   24.900000   
1999-01-08  1275.089966  23.280001   0.004221 -0.044727  0.181331   25.580000   
...                 ...        ...        ...       ...       ...         ...   
2020-07-23  3235.659912  26.080000  -0.012320  0.072368  0.195012   31.370001   
2020-07-24  3215.629883  25.840000  -0.006190 -0.009202  0.170433   33.840000   
2020-07-27  3239.409912  24.740000   0.007395 -0.042570  0.168660   32.220001   
2020-07-28  3218.439941  25.440001  -0.006473  0.028294  0.142532   34.730000   
2020-07-29  3258.439941  24.100000   0.012428 -0.052673  0.140448   31.780001   

            equity allocation  volatility allocation  portfolio_rets_1  \
Date                                                                     
1999-01-04                  1                      0          0.000000   
1999-01-05                  1                      0          0.021898   
1999-01-06                  1                      0          0.024262   
1999-01-07                  1                      0         -0.005141   
1999-01-08                  1                      0          0.011715   
...                       ...                    ...               ...   
2020-07-23                  1                      0         -0.011768   
2020-07-24                  1                      0         -0.005438   
2020-07-27                  1                      0          0.010158   
2020-07-28                  1                      0         -0.012624   
2020-07-29                  1                      0          0.012012   

            portfolio_cum_rets_1  ...  Risk_rets_on  Risk_cum_rets_on  \
Date                              ...                                   
1999-01-04              0.000000  ...      0.000000          0.000000   
1999-01-05              0.021898  ...      0.021898          0.021898   
1999-01-06              0.046691  ...      0.024262          0.046691   
1999-01-07              0.041310  ...     -0.005141          0.041310   
1999-01-08              0.053509  ...      0.011715          0.053509   
...                          ...  ...           ...               ...   
2020-07-23              3.876889  ...     -0.011768          2.923038   
2020-07-24              3.850367  ...     -0.005438          2.901703   
2020-07-27              3.899636  ...      0.010158          2.941336   
2020-07-28              3.837782  ...     -0.012624          2.891580   
2020-07-29              3.895892  ...      0.012012          2.938324   

            Risk_rets_off  Risk_cum_rets_off  portfolio_rets_2  \
Date                                                             
1999-01-04       0.000000           0.000000               NaN   
1999-01-05       0.011761           0.011761               NaN   
1999-01-06       0.013025           0.024940               NaN   
1999-01-07      -0.006546           0.018230               NaN   
1999-01-08       0.004651           0.022965               NaN   
...                   ...                ...               ...   
2020-07-23       0.000069           1.969775         -0.011768   
2020-07-24      -0.006296           1.951077         -0.005438   
2020-07-27       0.000132           1.951467          0.010158   
2020-07-28       0.005888           1.968845         -0.012624   
2020-07-29       0.005521           1.985235          0.012012   

            portfolio_cum_rets_2  rolling_max  rolling_max_GSPC  \
Date                                                              
1999-01-04                   NaN          NaN       1228.0

In [46]:
# Calculate Returns
def portfolio_analytics(weights):
    # Portfolio Return
    returns = weights[0]*df_risk_on['portfolio_rets_on'] + weights[1]*df_optimal['GLD_rets']
    cum_rets = (1 + returns).cumprod() -1
    port_ret = (cum_rets[-1] + 1)
    n = len(df_risk_on)
    port_ret_ann = (port_ret)**(252/n) - 1
    
    # Portfolio Volatility 
    port_std_ann = np.sqrt(252) * returns.std()
    return port_std_ann, port_ret_ann

In [47]:
# Generate Random Portfolios
num_portfolios = 5000
# Create DataFrame 
# Create DataFrame
df = pd.DataFrame(columns=['Equity Allocation','Volatility Allocation','Portfolio Returns','Portfolio Volatility','Portfolio SR'],index=range(num_portfolios))
num_assets = 2
results = np.zeros((3,num_portfolios))
weights_record = []
for i in range(num_portfolios):
    weights = np.random.random(num_assets)
    weights = weights/np.sum(weights)
    weights_record.append(weights)
    port_std_ann, port_ret_ann = portfolio_analytics(weights)
    df.loc[i,'Equity Allocation'] = weights[0]
    df.loc[i,'Volatility Allocation'] = weights[1]
    df.loc[i,'Portfolio Returns'] = port_ret_ann
    df.loc[i,'Portfolio Volatility'] = port_std_ann
    df.loc[i,'Portfolio SR'] = port_ret_ann/port_std_ann

In [48]:
sorted_df = df.sort_values('Portfolio SR',ascending=False)
sorted_df_return =df.sort_values('Portfolio Returns',ascending=False)
sorted_df_vol = df.sort_values('Portfolio Volatility',ascending=False)
sorted_df

Equity Allocation Volatility Allocation Portfolio Returns  \
3802          0.405441              0.594559         0.0708032   
4452            0.4053                0.5947          0.070804   
4339          0.405295              0.594705         0.0708041   
1128          0.405291              0.594709         0.0708041   
4605          0.406187              0.593813         0.0707988   
...                ...                   ...               ...   
493             0.9985            0.00149999         0.0574788   
4713          0.998626            0.00137401         0.0574739   
3106          0.998678            0.00132184         0.0574719   
2715          0.998731            0.00126892         0.0574698   
3392          0.999654           0.000346403         0.0574339   

     Portfolio Volatility Portfolio SR  
3802             0.141243     0.501288  
4452             0.141244     0.501288  
4339             0.141244     0.501288  
1128             0.141244     0.501288  
4605             0.141234     0.501288  
...                   ...          ...  
493              0.208276     0.275975  
4713               0.2083     0.275918  
3106             0.208311     0.275895  
2715             0.208321     0.275871  
3392             0.208504     0.275457  

[5000 rows x 5 columns]

In [49]:
sorted_df_return

Equity Allocation Volatility Allocation Portfolio Returns  \
2852          0.301434              0.698566         0.0711078   
3414          0.301335              0.698665         0.0711078   
4699          0.301794              0.698206         0.0711078   
3161          0.300959              0.699041         0.0711078   
2520          0.301934              0.698066         0.0711077   
...                ...                   ...               ...   
493             0.9985            0.00149999         0.0574788   
4713          0.998626            0.00137401         0.0574739   
3106          0.998678            0.00132184         0.0574719   
2715          0.998731            0.00126892         0.0574698   
3392          0.999654           0.000346403         0.0574339   

     Portfolio Volatility Portfolio SR  
2852             0.145182     0.489783  
3414             0.145188     0.489762  
4699             0.145159     0.489859  
3161             0.145212     0.489681  
2520             0.145151     0.489889  
...                   ...          ...  
493              0.208276     0.275975  
4713               0.2083     0.275918  
3106             0.208311     0.275895  
2715             0.208321     0.275871  
3392             0.208504     0.275457  

[5000 rows x 5 columns]

In [50]:
sorted_df_vol

Equity Allocation Volatility Allocation Portfolio Returns  \
3392          0.999654           0.000346403         0.0574339   
2715          0.998731            0.00126892         0.0574698   
3106          0.998678            0.00132184         0.0574719   
4713          0.998626            0.00137401         0.0574739   
493             0.9985            0.00149999         0.0574788   
...                ...                   ...               ...   
4761           0.42888               0.57112         0.0706505   
4251          0.428265              0.571735         0.0706549   
2569          0.428732              0.571268         0.0706516   
2308            0.4284                0.5716         0.0706539   
279           0.428591              0.571409         0.0706526   

     Portfolio Volatility Portfolio SR  
3392             0.208504     0.275457  
2715             0.208321     0.275871  
3106             0.208311     0.275895  
4713               0.2083     0.275918  
493              0.208276     0.275975  
...                   ...          ...  
4761             0.141106      0.50069  
4251             0.141106     0.500721  
2569             0.141106     0.500698  
2308             0.141106     0.500714  
279              0.141106     0.500705  

[5000 rows x 5 columns]

In [51]:
w_equity = sorted_df.iloc[0]['Equity Allocation']
w_vol = 1-w_equity
weights=[w_equity,w_vol]

In [52]:
std, ret = portfolio_analytics(weights)
print('Annualized Standard Deviation',std)
print('Annualized Return',ret)
print('SR',ret/std)

Annualized Standard Deviation 0.14124263178901586
Annualized Return 0.07080321617103102
SR 0.5012878567484838


In [139]:
df_optimal['Equity_Allocation'] = w_equity
# Create Vol Allocation
df_optimal['Volatility Allocation']= w_vol
# Portfolio Return
df_optimal['portfolio_rets_3'] = df_optimal['Equity_Allocation']*df_optimal['GSPC rets'] +df_optimal['Volatility Allocation']*df_optimal['GLD_rets']

In [141]:
df_portfolio = df_optimal[['portfolio_rets_3']]
df_portfolio['Cum Returns'] = (1 + df_optimal['portfolio_rets_3']).cumprod() -1

In [142]:
df_portfolio

portfolio_rets_3  Cum Returns
Date                                     
1999-01-04               NaN          NaN
1999-01-05               NaN          NaN
1999-01-06               NaN          NaN
1999-01-07               NaN          NaN
1999-01-08               NaN          NaN
...                      ...          ...
2020-07-23          0.000252     2.907797
2020-07-24          0.002591     2.917922
2020-07-27          0.014743     2.975684
2020-07-28          0.002335     2.984966
2020-07-29          0.009504     3.022840

[5428 rows x 2 columns]

In [146]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Create a figure
fig = go.Figure()

# Add trace, x axis, y axis, mode = lines
fig.add_trace(go.Scatter(x=df_optimal.index, y=df_optimal["GSPC_cum_rets"]*100, mode='lines',line=dict(color='red',width=2), name='SPY'))
fig.add_trace(go.Scatter(x=df_optimal.index, y=df_portfolio['Cum Returns']*100, mode='lines',line=dict(color='royalblue',width=2), name='portfolio_3'))



# Update Layout
fig.update_layout(
    title={'text':'Simulated Portfolio Optimization',
           'y':0.9,
        'x':0.5,
          'xanchor': 'center',
             'yanchor': 'top' },
    
    xaxis=dict(
        title='',
        #ticksuffix="%",
        #tickprefix=''
    ),
    
    yaxis=dict(
        title='',
         ticksuffix="%"
    ),
    
 
    paper_bgcolor='rgba(0,0,0,0)',
    plot_bgcolor='rgba(0,0,0,0)',
)